In [1]:
import numpy as np
import sqlite3
from scipy.spatial import distance #https://docs.scipy.org/doc/scipy/reference/generated/scipy.spatial.distance.cdist.html


In [5]:
conn = sqlite3.connect('../livs.db')  # Create db and establish connection
conn.row_factory = sqlite3.Row
curs = conn.cursor()
result = []
columnObject=[]
rows = curs.execute('select * from livs')
for row in rows:
        result.append(row)

db_contents = np.array(result)
for row in conn.execute('PRAGMA table_info (livs);'):
    columnObject.append(row)

conn.close()

In [8]:
columns = np.array(columnObject)
columns

array([[0, 'Livsmedelsnamn', 'TEXT', 0, None, 0],
       [1, 'Livsmedelsnummer', 'TEXT', 0, None, 0],
       [2, 'Energi_kcal', 'REAL', 0, None, 0],
       [3, 'Energi_kJ', 'REAL', 0, None, 0],
       [4, 'Kolhydrater_g', 'REAL', 0, None, 0],
       [5, 'Fett_g', 'REAL', 0, None, 0],
       [6, 'Protein_g', 'REAL', 0, None, 0],
       [7, 'Fibrer_g', 'REAL', 0, None, 0],
       [8, 'Vatten_g', 'REAL', 0, None, 0],
       [9, 'Alkohol_g', 'REAL', 0, None, 0],
       [10, 'Aska_g', 'REAL', 0, None, 0],
       [11, 'Monosackarider_g', 'REAL', 0, None, 0],
       [12, 'Disackarider_g', 'REAL', 0, None, 0],
       [13, 'Sackaros_g', 'REAL', 0, None, 0],
       [14, 'Fullkorn_totalt_g', 'REAL', 0, None, 0],
       [15, 'Sockerarter_g', 'REAL', 0, None, 0],
       [16, 'Summa_mattade_fettsyror_g', 'REAL', 0, None, 0],
       [17, 'Fettsyra_4_0_10_0_g', 'REAL', 0, None, 0],
       [18, 'Fettsyra_12_0_g', 'REAL', 0, None, 0],
       [19, 'Fettsyra_14_0_g', 'REAL', 0, None, 0],
       [20, 'Fett

In [10]:
import pickle
import requests
#Skapa picklad fil från np.array (db_contents)
with open('columns.npy', 'wb') as pickle_file:
    pickle.dump(columns, pickle_file)

## Prototypiska i sin kategori
Syftet är att ta en huvudgrupp och se vad mittpunkten i den kategorin är och sen räkna ut vilka livsmedel som ligger närmast mittpunkten.

Varje näringsvärde blir en dimension, och varje livsmedel en punkt som har ett värde i alla de dimensionerna.

Medelvärdet av alla livsmedel blir en punkt som man kan utgå från när man räknar avstånd till alla livsmedlen, och när man har tillgång till avstånden så kan man ordna alla livsmedlen efter avståndet till mittpunkten.

Det är första steget. 

Andra steget är att se om man verkligen behöver alla näringsvärden för att ändå få samma ordning mellan livsmedlen. Vilka kan man ta bort?

### Utgångspunkter

Från Livsmedelsverkets data har vi valt en huvudgrupp, som "Grönsaker". Alla dess data ligger i db_contents, och den variabeln har en shape som säger hur många rader (livsmedel) och kolumner (namn, nummer, näringsvärden, klassificering) den innehåller.

In [29]:
db_contents.shape

(2088, 63)

Kolumn 0 är namnet, 1 är numret och sen börjar näringsvärdena. 

columns är variabeln som innehåller de värden som används i beräkningarna. Under står de kolumner som är möjliga att använda. 

Vill man ha fram betydelsena av kolumnerna kan man göra något i stil med

```
for row in conn.execute('PRAGMA table_info (livs);'):
    columnObject.append(row)
columns = np.array(columnObject)
``` 

In [30]:
columns = np.array([ 2,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 35, 37, 38, 40, 41, 42, 43, 44, 45, 46, 47, 48, 50, 51, 52, 53, 54, 55, 56, 57])
# Possible columns: [ 2,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 35, 37, 38, 40, 41, 42, 43, 44, 45, 46, 47, 48, 50, 51, 52, 53, 54, 55, 56, 57]


dataset blir de kolumner som används. Från databasen brukar de komma som unicode, så det är lämpligt att konvertera till float.

In [31]:
dataset = db_contents[:,columns].astype(float)

Det är fantastiskt enkelt att räkna medelvärdet av varje kolumn med funktionen numpy.mean, som returnerar en array med lika många element som antal kolumner

Obs: axis behövs, för annars får man fel medelvärde...

In [32]:
means = np.mean(dataset, axis=0)

In [33]:
print(means, '\n', means.shape)

[  2.00138506e+02   1.74014320e+01   1.02246456e+01   8.39439176e+00
   1.81404693e+00   5.98207759e+01   2.01178161e-01   2.11484674e+00
   2.07985153e+00   4.58032088e+00   3.65994732e+00   3.31130268e+00
   3.54142720e+00   1.90986590e-01   2.52744253e-01   3.24415709e-01
   1.86707375e+00   7.55560345e-01   3.07279693e-02   3.97260057e+00
   1.61963602e-01   3.65182471e+00   1.99562261e+00   1.49247605e+00
   3.14056513e-01   2.14750958e-02   3.38601533e-02   1.41666667e-02
   5.89128352e-02   3.42085632e+01   1.95642050e+02   9.62835249e-01
   1.61956418e+00   1.37452107e-01   1.74157088e-01   6.38864943e+00
   2.16066092e+00   3.70530651e+00   1.76934866e-01   1.24941092e+00
   3.38202107e+01   1.34543391e+02   1.44270115e+00   6.25349617e+01
   2.42284483e+02   2.84714559e+01   4.90996169e+02   1.22861590e+00
   6.67829502e+00   1.18068966e+00] 
 (50,)


Det är läskigt lätt även att räkna avståndet mellan alla punkterna i dataset och medelvärdena:

(Det är något med medelvärdena som gör att man måste sätta en extra klammer runt, för att dimensionaliteten ska stämma...)

In [34]:
dist = distance.cdist(dataset, [means], 'euclidean') #https://docs.scipy.org/doc/scipy/reference/generated/scipy.spatial.distance.cdist.html

*dist* innehåller sen varje rads avstånd från medelvärdet i alla kolumner.

In [35]:
dist

array([[  748.74328448],
       [  803.07420312],
       [  918.8334398 ],
       ..., 
       [  576.95976402],
       [ 7626.50413789],
       [  345.70650167]])

Jag har svårt att vänja mig vid det här med implicit sortering.

Först sorterar vi alltså värdena och får en "ordning", som vi sen använder som index för den array vi egentligen vill sortera...

In [36]:
order = np.argsort(dist.T[0])

In [37]:
order

array([1792,  657,  907, ..., 1684, 1682, 1207])

Eftersom vi har vår ursprungliga lista med oss i *db_contents* så kan vi skriva ut vilka kolumner som helst, och nu med raderna i rätt ordning utifrån medelvärdet i huvudgruppen.

Här tog det ett tag för mig att förstå hur jag skulle se på resultatet. Att se de första som näringsmässigt "lika" var inte så svårt, men hur är det med de livsmedel som hamnar sist i listan?

Jag tror att man ska se det som en (mångdimensionell) "periferi" där de sista i listan förstås är långt från centrum, men inte alls inbördes "lika". De kan ha stort avstånd till mitten i väldigt skilda dimensioner. Det enda som förenar dem är att de är udda... :-)

In [38]:
db_contents[order,0]

array(['Paj skinka broccoli', 'Paj lax spenat', 'Kalvfrikassé fryst', ...,
       'Havssalt', 'Joderat salt', 'Lamm lever rå'], dtype=object)

## Del två. Att jämföra ordningar...

Den här ordningen mellan livsmedel bygger på att man tar ett urval kolumner. Typiskt tar man så mycket information man har (= alla kolumner) för att få en mer relevant ordning.

Men kanske är det så att inte alla kolumner behövs för att ge den här ordningen? Vilka kolumner skulle man kunna ta bort?

Det enklaste är att kolla om ordningarna är identiska, så i nedanstående är det bara det som görs. 

Dags att summera ihop mycket av del 1 i en funktion. Utgå från db_contents som typ en global variabel. Skicka in kolumner till funktionen, så returneras en ordning mellan livsmedlen i db_contents/dataset

In [39]:
def get_order(columns):
    dataset = db_contents[:,columns].astype(float)
    means = np.mean(dataset, axis=0)
    dist = distance.cdist(dataset, [means], 'euclidean')
    order = np.argsort(dist.T[0])
    return order

Vi ska jämföra ursprungsordningen (order_0) med alla ordningar som uppkommer när man tar bort en kolumn. Vi kallar underordningarna för order_1 och löper igenom dem en i taget.

In [40]:
columns_0 = columns
order_0 = get_order(columns)

In [41]:
order_0

array([1792,  657,  907, ..., 1684, 1682, 1207])

Här är ett exempel på vad som händer när man tar bort en kolumn:

In [42]:
columns_1 = np.delete(columns,4)

In [43]:
columns_1

array([ 2,  4,  5,  6,  8,  9, 10, 11, 12, 13, 14, 16, 17, 18, 19, 20, 21,
       22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 35, 37, 38, 40, 41,
       42, 43, 44, 45, 46, 47, 48, 50, 51, 52, 53, 54, 55, 56, 57])

In [44]:
order_1 = get_order(columns_1)

In [45]:
x = np.array_equal(order_0, order_1)

In [46]:
x

False

In [47]:
columns_1

array([ 2,  4,  5,  6,  8,  9, 10, 11, 12, 13, 14, 16, 17, 18, 19, 20, 21,
       22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 35, 37, 38, 40, 41,
       42, 43, 44, 45, 46, 47, 48, 50, 51, 52, 53, 54, 55, 56, 57])

Om vi tar en uppsättning kolumner behöver vi loopa igenom alla uppsättningar som saknar en kolumn. Något i den här stilen:

In [48]:
size = columns.size
print(size)
a = np.empty([size,size-1],dtype=int)
#print(a)
for index, item in enumerate(columns):
    a[index]=np.delete(columns,index)
    print(a[index])

50
[ 4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 22 23 24 25 26 27 28 29
 30 31 32 33 35 37 38 40 41 42 43 44 45 46 47 48 50 51 52 53 54 55 56 57]
[ 2  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 22 23 24 25 26 27 28 29
 30 31 32 33 35 37 38 40 41 42 43 44 45 46 47 48 50 51 52 53 54 55 56 57]
[ 2  4  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 22 23 24 25 26 27 28 29
 30 31 32 33 35 37 38 40 41 42 43 44 45 46 47 48 50 51 52 53 54 55 56 57]
[ 2  4  5  7  8  9 10 11 12 13 14 16 17 18 19 20 21 22 23 24 25 26 27 28 29
 30 31 32 33 35 37 38 40 41 42 43 44 45 46 47 48 50 51 52 53 54 55 56 57]
[ 2  4  5  6  8  9 10 11 12 13 14 16 17 18 19 20 21 22 23 24 25 26 27 28 29
 30 31 32 33 35 37 38 40 41 42 43 44 45 46 47 48 50 51 52 53 54 55 56 57]
[ 2  4  5  6  7  9 10 11 12 13 14 16 17 18 19 20 21 22 23 24 25 26 27 28 29
 30 31 32 33 35 37 38 40 41 42 43 44 45 46 47 48 50 51 52 53 54 55 56 57]
[ 2  4  5  6  7  8 10 11 12 13 14 16 17 18 19 20 21 22 23 24 25 26 27 28 29
 30 31 32 33 35 37 38

Om vi ska göra en funktion av det hela och få ut en array av de överflödiga kolumnerna:

In [49]:
def remove_dimensions (columns):
    columns_1 = np.empty([columns.size,columns.size-1],dtype=int)
    superfluous = []
    #print(a)
    for index, item in enumerate(columns):
        columns_1[index]=np.delete(columns,index)
        if np.array_equal(get_order(columns), get_order(columns_1[index])):
            superfluous.append(item)
    return superfluous

In [50]:
print (columns_0)
superfluous = remove_dimensions (columns_0)
superfluous

[ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 22 23 24 25 26 27 28
 29 30 31 32 33 35 37 38 40 41 42 43 44 45 46 47 48 50 51 52 53 54 55 56 57]


[22, 24, 29, 30, 31, 41, 45]

In [51]:
columns

array([ 2,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 16, 17, 18, 19, 20,
       21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 35, 37, 38, 40,
       41, 42, 43, 44, 45, 46, 47, 48, 50, 51, 52, 53, 54, 55, 56, 57])

dim_superfluous är den listan som växer i varje "ben" av rekursionen. När funktionen bottnar appendas den till superlist och kapas

superfluous är resultatet av remove_dimensions, dvs en eller flera överflödiga dimensioner. Att superfluous blir tom är det samma som att algoritmen bottnar

dim_orig är listan som varje varv skickas till rekursionen. Den kapas med den överflödiga dimensionen för varje varv.

In [52]:
dim_superfluous = []
#Rekursiv
def reduce (dim_orig, dim_superfluous ):
    print ('-> reduce: första raden', 'dim_orig:', dim_orig, 'dim_superfluous', dim_superfluous)
    superfluous = remove_dimensions (dim_orig)
    print ('vi beräknar superfluous till',superfluous)
    if superfluous == []:
        print ('<- bottnar')
        superlist.append(dim_superfluous[:])
        # https://stackoverflow.com/questions/40425554/python-shallow-copy-and-deep-copy-in-using-append-method?rq=1
        print ('superlist', superlist)
        return 
    else:
        for index, superfluou in enumerate(superfluous):
            print ('i for-loopen –', 'index:', index, 'superfluou:', superfluou, 'superfluous:', superfluous, )
            new_dim_superfluous = dim_superfluous[:]
            new_dim_superfluous.append(superfluou)
            print ('new_dim_superfluous efter lagt till superfluou', new_dim_superfluous)            
            new_dim_orig = dim_orig[:]
            new_dim_orig = np.delete(new_dim_orig, np.where(new_dim_orig==superfluou), 0)
            print ('dim_orig efter tagit bort superflou:', dim_orig)
            reduce (new_dim_orig, new_dim_superfluous)
        return 


In [ ]:
superlist=[]
x = reduce (columns, [])
x

-> reduce: första raden dim_orig: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 22 23 24 25 26 27 28
 29 30 31 32 33 35 37 38 40 41 42 43 44 45 46 47 48 50 51 52 53 54 55 56 57] dim_superfluous []
vi beräknar superfluous till [22, 24, 29, 30, 31, 41, 45]
i for-loopen – index: 0 superfluou: 22 superfluous: [22, 24, 29, 30, 31, 41, 45]
new_dim_superfluous efter lagt till superfluou [22]
dim_orig efter tagit bort superflou: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 22 23 24 25 26 27 28
 29 30 31 32 33 35 37 38 40 41 42 43 44 45 46 47 48 50 51 52 53 54 55 56 57]
-> reduce: första raden dim_orig: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 24 25 26 27 28 29
 30 31 32 33 35 37 38 40 41 42 43 44 45 46 47 48 50 51 52 53 54 55 56 57] dim_superfluous [22]
vi beräknar superfluous till [24, 29, 30, 31, 41, 45]
i for-loopen – index: 0 superfluou: 24 superfluous: [24, 29, 30, 31, 41, 45]
new_dim_superfluous efter lagt till superfluou [22, 24]
dim_orig efter tagit 

vi beräknar superfluous till []
<- bottnar
superlist [[22, 24, 29, 30, 31, 41, 45], [22, 24, 29, 30, 31, 45, 41], [22, 24, 29, 30, 41, 31, 45], [22, 24, 29, 30, 41, 45, 31]]
i for-loopen – index: 2 superfluou: 45 superfluous: [31, 41, 45]
new_dim_superfluous efter lagt till superfluou [22, 24, 29, 30, 45]
dim_orig efter tagit bort superflou: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 25 26 27 28 31 32
 33 35 37 38 40 41 42 43 44 45 46 47 48 50 51 52 53 54 55 56 57]
-> reduce: första raden dim_orig: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 25 26 27 28 31 32
 33 35 37 38 40 41 42 43 44 46 47 48 50 51 52 53 54 55 56 57] dim_superfluous [22, 24, 29, 30, 45]
vi beräknar superfluous till [31, 41]
i for-loopen – index: 0 superfluou: 31 superfluous: [31, 41]
new_dim_superfluous efter lagt till superfluou [22, 24, 29, 30, 45, 31]
dim_orig efter tagit bort superflou: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 25 26 27 28 31 32
 33 35 37 38 40 41 42 

vi beräknar superfluous till [45]
i for-loopen – index: 0 superfluou: 45 superfluous: [45]
new_dim_superfluous efter lagt till superfluou [22, 24, 29, 31, 41, 30, 45]
dim_orig efter tagit bort superflou: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 25 26 27 28 32 33
 35 37 38 40 42 43 44 45 46 47 48 50 51 52 53 54 55 56 57]
-> reduce: första raden dim_orig: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 25 26 27 28 32 33
 35 37 38 40 42 43 44 46 47 48 50 51 52 53 54 55 56 57] dim_superfluous [22, 24, 29, 31, 41, 30, 45]
vi beräknar superfluous till []
<- bottnar
superlist [[22, 24, 29, 30, 31, 41, 45], [22, 24, 29, 30, 31, 45, 41], [22, 24, 29, 30, 41, 31, 45], [22, 24, 29, 30, 41, 45, 31], [22, 24, 29, 30, 45, 31, 41], [22, 24, 29, 30, 45, 41, 31], [22, 24, 29, 31, 30, 41, 45], [22, 24, 29, 31, 30, 45, 41], [22, 24, 29, 31, 41, 30, 45]]
i for-loopen – index: 1 superfluou: 45 superfluous: [30, 45]
new_dim_superfluous efter lagt till superfluou [22, 24, 29, 31, 4

vi beräknar superfluous till [31]
i for-loopen – index: 0 superfluou: 31 superfluous: [31]
new_dim_superfluous efter lagt till superfluou [22, 24, 29, 41, 30, 45, 31]
dim_orig efter tagit bort superflou: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 25 26 27 28 31 32
 33 35 37 38 40 42 43 44 46 47 48 50 51 52 53 54 55 56 57]
-> reduce: första raden dim_orig: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 25 26 27 28 32 33
 35 37 38 40 42 43 44 46 47 48 50 51 52 53 54 55 56 57] dim_superfluous [22, 24, 29, 41, 30, 45, 31]
vi beräknar superfluous till []
<- bottnar
superlist [[22, 24, 29, 30, 31, 41, 45], [22, 24, 29, 30, 31, 45, 41], [22, 24, 29, 30, 41, 31, 45], [22, 24, 29, 30, 41, 45, 31], [22, 24, 29, 30, 45, 31, 41], [22, 24, 29, 30, 45, 41, 31], [22, 24, 29, 31, 30, 41, 45], [22, 24, 29, 31, 30, 45, 41], [22, 24, 29, 31, 41, 30, 45], [22, 24, 29, 31, 41, 45, 30], [22, 24, 29, 31, 45, 30, 41], [22, 24, 29, 31, 45, 41, 30], [22, 24, 29, 41, 30, 31, 45], [22, 2

vi beräknar superfluous till [30, 31, 41]
i for-loopen – index: 0 superfluou: 30 superfluous: [30, 31, 41]
new_dim_superfluous efter lagt till superfluou [22, 24, 29, 45, 30]
dim_orig efter tagit bort superflou: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 25 26 27 28 30 31
 32 33 35 37 38 40 41 42 43 44 46 47 48 50 51 52 53 54 55 56 57]
-> reduce: första raden dim_orig: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 25 26 27 28 31 32
 33 35 37 38 40 41 42 43 44 46 47 48 50 51 52 53 54 55 56 57] dim_superfluous [22, 24, 29, 45, 30]
vi beräknar superfluous till [31, 41]
i for-loopen – index: 0 superfluou: 31 superfluous: [31, 41]
new_dim_superfluous efter lagt till superfluou [22, 24, 29, 45, 30, 31]
dim_orig efter tagit bort superflou: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 25 26 27 28 31 32
 33 35 37 38 40 41 42 43 44 46 47 48 50 51 52 53 54 55 56 57]
-> reduce: första raden dim_orig: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 

...

vi beräknar superfluous till [24]
i for-loopen – index: 0 superfluou: 24 superfluous: [24]
new_dim_superfluous efter lagt till superfluou [22, 45, 29, 31, 30, 41, 24]
dim_orig efter tagit bort superflou: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 24 25 26 27 28 32
 33 35 37 38 40 42 43 44 46 47 48 50 51 52 53 54 55 56 57]
-> reduce: första raden dim_orig: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 25 26 27 28 32 33
 35 37 38 40 42 43 44 46 47 48 50 51 52 53 54 55 56 57] dim_superfluous [22, 45, 29, 31, 30, 41, 24]
vi beräknar superfluous till []
<- bottnar
superlist [[22, 24, 29, 30, 31, 41, 45], [22, 24, 29, 30, 31, 45, 41], [22, 24, 29, 30, 41, 31, 45], [22, 24, 29, 30, 41, 45, 31], [22, 24, 29, 30, 45, 31, 41], [22, 24, 29, 30, 45, 41, 31], [22, 24, 29, 31, 30, 41, 45], [22, 24, 29, 31, 30, 45, 41], [22, 24, 29, 31, 41, 30, 45], [22, 24, 29, 31, 41, 45, 30], [22, 24, 29, 31, 45, 30, 41], [22, 24, 29, 31, 45, 41, 30], [22, 24, 29, 41, 30, 31, 45], [22, 2

vi beräknar superfluous till [24, 30]
i for-loopen – index: 0 superfluou: 24 superfluous: [24, 30]
new_dim_superfluous efter lagt till superfluou [22, 45, 29, 31, 41, 24]
dim_orig efter tagit bort superflou: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 24 25 26 27 28 30
 32 33 35 37 38 40 42 43 44 46 47 48 50 51 52 53 54 55 56 57]
-> reduce: första raden dim_orig: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 25 26 27 28 30 32
 33 35 37 38 40 42 43 44 46 47 48 50 51 52 53 54 55 56 57] dim_superfluous [22, 45, 29, 31, 41, 24]
vi beräknar superfluous till [30]
i for-loopen – index: 0 superfluou: 30 superfluous: [30]
new_dim_superfluous efter lagt till superfluou [22, 45, 29, 31, 41, 24, 30]
dim_orig efter tagit bort superflou: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 25 26 27 28 30 32
 33 35 37 38 40 42 43 44 46 47 48 50 51 52 53 54 55 56 57]
-> reduce: första raden dim_orig: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 25 26 27 28 3

vi beräknar superfluous till [24]
i for-loopen – index: 0 superfluou: 24 superfluous: [24]
new_dim_superfluous efter lagt till superfluou [22, 45, 29, 31, 41, 30, 24]
dim_orig efter tagit bort superflou: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 24 25 26 27 28 32
 33 35 37 38 40 42 43 44 46 47 48 50 51 52 53 54 55 56 57]
-> reduce: första raden dim_orig: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 25 26 27 28 32 33
 35 37 38 40 42 43 44 46 47 48 50 51 52 53 54 55 56 57] dim_superfluous [22, 45, 29, 31, 41, 30, 24]
vi beräknar superfluous till []
<- bottnar
superlist [[22, 24, 29, 30, 31, 41, 45], [22, 24, 29, 30, 31, 45, 41], [22, 24, 29, 30, 41, 31, 45], [22, 24, 29, 30, 41, 45, 31], [22, 24, 29, 30, 45, 31, 41], [22, 24, 29, 30, 45, 41, 31], [22, 24, 29, 31, 30, 41, 45], [22, 24, 29, 31, 30, 45, 41], [22, 24, 29, 31, 41, 30, 45], [22, 24, 29, 31, 41, 45, 30], [22, 24, 29, 31, 45, 30, 41], [22, 24, 29, 31, 45, 41, 30], [22, 24, 29, 41, 30, 31, 45], [22, 2

vi beräknar superfluous till [24, 30, 31]
i for-loopen – index: 0 superfluou: 24 superfluous: [24, 30, 31]
new_dim_superfluous efter lagt till superfluou [22, 45, 29, 41, 24]
dim_orig efter tagit bort superflou: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 24 25 26 27 28 30
 31 32 33 35 37 38 40 42 43 44 46 47 48 50 51 52 53 54 55 56 57]
-> reduce: första raden dim_orig: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 25 26 27 28 30 31
 32 33 35 37 38 40 42 43 44 46 47 48 50 51 52 53 54 55 56 57] dim_superfluous [22, 45, 29, 41, 24]
vi beräknar superfluous till [30, 31]
i for-loopen – index: 0 superfluou: 30 superfluous: [30, 31]
new_dim_superfluous efter lagt till superfluou [22, 45, 29, 41, 24, 30]
dim_orig efter tagit bort superflou: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 25 26 27 28 30 31
 32 33 35 37 38 40 42 43 44 46 47 48 50 51 52 53 54 55 56 57]
-> reduce: första raden dim_orig: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 

vi beräknar superfluous till [30]
i for-loopen – index: 0 superfluou: 30 superfluous: [30]
new_dim_superfluous efter lagt till superfluou [22, 45, 29, 41, 24, 31, 30]
dim_orig efter tagit bort superflou: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 25 26 27 28 30 32
 33 35 37 38 40 42 43 44 46 47 48 50 51 52 53 54 55 56 57]
-> reduce: första raden dim_orig: [ 2  4  5  6  7  8  9 10 11 12 13 14 16 17 18 19 20 21 23 25 26 27 28 32 33
 35 37 38 40 42 43 44 46 47 48 50 51 52 53 54 55 56 57] dim_superfluous [22, 45, 29, 41, 24, 31, 30]
vi beräknar superfluous till []
<- bottnar
superlist [[22, 24, 29, 30, 31, 41, 45], [22, 24, 29, 30, 31, 45, 41], [22, 24, 29, 30, 41, 31, 45], [22, 24, 29, 30, 41, 45, 31], [22, 24, 29, 30, 45, 31, 41], [22, 24, 29, 30, 45, 41, 31], [22, 24, 29, 31, 30, 41, 45], [22, 24, 29, 31, 30, 45, 41], [22, 24, 29, 31, 41, 30, 45], [22, 24, 29, 31, 41, 45, 30], [22, 24, 29, 31, 45, 30, 41], [22, 24, 29, 31, 45, 41, 30], [22, 24, 29, 41, 30, 31, 45], [22, 2